#Продвинутый Python, ДЗ-4

Правила игры:

В домашке 6 задач, разбаловка указана в задании. Суммарно за дз можно получить 100 баллов, что равняется 10 баллам

Дедлайн - 7 дней после выдачи дз. Необходимо залить решеннный ноутбук в github и прислать ссылку в Anytask (без выполнения любого из пунктов работа проверяться не будет)

В данной домашке нужно рисовать графики с помощью plotly или же Dash. Обратите внимание, что все графики и оси должны быть подписаны, графики должны выглядеть аккуратно (за это будем штрафовать)

## Данные

В этом домашнем задании вам придется оказаться на месте аналитика в бразильском маркетплейсе [Olist](https://olist.com/pt-br/). Вам необходимо исследовать данные и на их основании сделать выводы, которые помогут бизнесу расцветать!

Данные находятся тут в файле archive.zip

In [2]:
!pip install wget

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import zipfile
import wget

url = 'https://github.com/Palladain/Deep_Python/raw/main/Homeworks/Homework_1/archive.zip'
filename = wget.download(url)

with zipfile.ZipFile(filename, 'r') as zip_ref:
    zip_ref.extractall('./')

customers = pd.read_csv('olist_customers_dataset.csv')
location = pd.read_csv('olist_geolocation_dataset.csv')
items = pd.read_csv('olist_order_items_dataset.csv')
payments = pd.read_csv('olist_order_payments_dataset.csv')
reviews = pd.read_csv('olist_order_reviews_dataset.csv')
orders = pd.read_csv('olist_orders_dataset.csv')
products = pd.read_csv('olist_products_dataset.csv')
translation = pd.read_csv('product_category_name_translation.csv')
sellers = pd.read_csv('olist_sellers_dataset.csv')

Ван дано 9 датасетов, которые содержат в себе все данные по 100 000 заказам со всей Бразилии. Чтобы облегчить вам жизнь, вот связи по этим датасетам (файл product_category_name_translation является переводом названий категорий с португальского на английский)

![](https://i.imgur.com/HRhd2Y0.png)

Ну что же, начнем!

# Часть 1. Plotly

В данной части для заданий нужно использовать Plotly для того, чтобы отобразить графики

## Задание 1 (15 баллов)

Отобразите на карте всех продавцов (в качестве точек - координаты, в качестве размера и цвета точек - число продавцов). При наведении точек должно отображаться название штата, города, а также число продавцов

*Hint: внимательно посмотрите на датасет locations. Если делать задачу максимально втупую, то у вас либо крашнется/зависнет отрисовка, либо на это нельзя будет нормально смотреть*

In [4]:
!pip install nbformat

In [5]:
import pandas as pd
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns
from dateutil.parser import parse

import plotly
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots

In [6]:
location['sel_count'] = 1
df = location.groupby(['geolocation_zip_code_prefix', 'geolocation_city', 'geolocation_state']) \
    .agg({'geolocation_lat': 'mean', 'geolocation_lng': 'mean', 'sel_count': 'count'})\
    .reset_index().rename(columns={'geolocation_lat': 'latitude', 'geolocation_lng': 'longitude', 'sel_count': 'sellers'})
fig = px.scatter_mapbox(df, 
                        lat="latitude", 
                        lon="longitude", 
                        size="sellers", 
                        color="sellers",
                        zoom=5, 
                        mapbox_style="open-street-map",
                        text=df["geolocation_city"] + ', ' + df["geolocation_state"])
fig.show()

## Задание 2 (15 баллов)

Отобразите на графике число заказов по дням с разбивкой по статусам. Также создайте график со средней оценкой отзыва (аггрегируйте по дням). Для обоих графиков должен быть слайдер по датам

In [7]:
def strip_date(x):
    x = x.replace(hour=0)
    x = x.replace(minute=0)
    x = x.replace(second=0)
    return x

fig = go.Figure()

cols = ['order_purchase_timestamp', 'order_delivered_carrier_date', 'order_delivered_customer_date']

for col in cols:
    df = orders
    df[col] = pd.to_datetime(df[col])
    df[col] = df[col].apply(lambda x: strip_date(x))
    df = df.groupby(col).agg({"order_id": "nunique"}).reset_index()

    fig.add_trace(go.Scatter(x=df[col], y=df["order_id"], visible=True, opacity=0.6))

updatemenu = [dict()]

buttons = []

for i, col in enumerate(cols):
    visibles = [False] * len(cols)
    visibles[i] = True
    buttons.append(dict(method='restyle',
                        label=col,
                        args=["visible", visibles]
                        ))

updatemenu[0]['buttons']=buttons
updatemenu[0]['direction']='down'
updatemenu[0]['showactive']=True

fig.update_layout(showlegend=False, updatemenus = updatemenu)
go.layout.Updatemenu(x=0, y=1)

fig.update_layout(
    title = {
        "text": "Number of orders",
        "x": 0.5
    }
)

fig.update_layout(
    xaxis=dict(
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)

fig.show()

/opt/homebrew/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/opt/homebrew/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/opt/homebrew/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [8]:
def strip_date(x):
    x = x.replace(hour=0)
    x = x.replace(minute=0)
    x = x.replace(second=0)
    return x

fig = go.Figure()

df = reviews

df['review_creation_date'] = pd.to_datetime(df['review_creation_date'])
df['review_creation_date'] = df['review_creation_date'].apply(lambda x: strip_date(x))
df = df.groupby('review_creation_date').agg({"review_score": "mean"}).reset_index()

fig.add_trace(go.Scatter(x=df['review_creation_date'], y=df["review_score"], visible=True, opacity=0.6))

fig.update_layout(
    title = {
        "text": "Average review scores",
        "x": 0.5
    }
)

fig.update_layout(
    xaxis=dict(
        rangeslider=dict(
            visible=True
        ),
        type="date"
    )
)

fig.show()

/opt/homebrew/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



## Задание 3 (20 баллов)

Выберите топ-5 продавцов с более чем 20 продажами, которые чаще всего отсылают свою посылку в другие регионы и визуализируйте их отсылки

In [9]:
# код взят с аналогичного задания номер 8 в дз номер 2
df = orders[orders['order_status'] == 'delivered']

df = pd.merge(df[['order_id', 'customer_id']], items[['order_id', 'seller_id']], on='order_id', how='inner')
df = pd.merge(df, customers[['customer_id', 'customer_state']], on='customer_id', how='inner').drop_duplicates(subset=['seller_id', 'order_id'])

df = pd.merge(df[['customer_state', 'seller_id']], sellers[['seller_id', 'seller_state']], on='seller_id')
df['share'] = df.apply(lambda x: x.customer_state != x.seller_state, axis=1)
agg_func={'share':'sum', 'customer_state':'count'}
res = df.groupby('seller_id').agg(agg_func).reset_index()

res['share'] = res.apply(lambda x: x.share/x.customer_state, axis=1)
res = res[res.customer_state > 20].sort_values('share', ascending=False)[:5]
res

seller_id  share  customer_state
2864  f62d7bb4a613ec758a03342d46b580b2    1.0              32
1218  679769a98cfcc6da877c8486ff1c13f3    1.0              21
1506  7ecd59e5e20407131822c1a68ac59c1f    1.0              24
1563  83deb69e889cf80f82be1dc6d5f2d486    1.0              40
645   38e679b9e0064cd94c6f035707344dae    1.0              27

In [10]:
df = sellers[sellers['seller_id'].isin(res['seller_id'].values)]

df_ord = orders[orders['order_status'] == 'delivered']

df = pd.merge(df_ord[['order_id', 'customer_id']], items[['order_id', 'seller_id']], on='order_id', how='inner')
df = pd.merge(df, customers[['customer_id', 'customer_state', 'customer_city', 'customer_zip_code_prefix']], on='customer_id', how='inner').drop_duplicates(subset=['seller_id', 'order_id'])

df = pd.merge(df[['customer_state', 'seller_id', 'customer_id', 'customer_city', 'customer_zip_code_prefix']], sellers[['seller_id', 'seller_state']], on='seller_id')
df = pd.merge(df.rename(columns={'customer_zip_code_prefix': 'geolocation_zip_code_prefix'}), location, on='geolocation_zip_code_prefix')
df = df[df['seller_id'].isin(res['seller_id'].values)]

fig = px.scatter_mapbox(df, 
                        lat='geolocation_lat', 
                        lon="geolocation_lng", 
                        zoom=5, 
                        color='seller_id',
                        mapbox_style="open-street-map",
                        text=df["geolocation_city"] + ', ' + df["geolocation_state"])

fig.show()

# Часть 2. Dash

В данной части нужно сделать и сдать один .py файл (можно назвать dash_task.py), который будет разворачивать страничку с нарисованными графиками (с помощью Dash)

## Задание 4 (20 баллов)

Сделайте сайт, где будет отображаться следующее:

* График, показывающий распределение по категориям продаж (то есть по тому, что продают селлеры) в штате

* График, показывающий распределение по категориям покупок (то есть по тому, что покупают пользователи) в штате

* Фильтр по штатам (должна быть возможность как выбрать отдельный штат, так и вся Бразилия в целом)

* Возможность выбрать, какие статусы продаж учитывать (чтобы можно было выбрать несколько статусов)

* Слайдер по датам (чтобы можно было выбрать даты, по которым можем смотреть результаты)


In [11]:
from dash import Dash, html, dcc, Input, Output
import plotly.express as px
import pandas as pd
import numpy as np
from datetime import datetime as dt

import matplotlib.pyplot as plt
import seaborn as sns
from dateutil.parser import parse

import plotly
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots


In [12]:
df = pd.merge(products[['product_id', 'product_category_name']], pd.merge(items, orders, on='order_id'), on='product_id')[['order_id', 'seller_id', 'order_status', 'product_category_name', 'order_purchase_timestamp', 'order_delivered_customer_date']].drop_duplicates()
df = pd.merge(df, sellers[['seller_id', 'seller_zip_code_prefix']], on='seller_id').drop_duplicates(subset=['order_id', 'product_category_name'])
df = pd.merge(df.rename(columns={'seller_zip_code_prefix': 'geolocation_zip_code_prefix'}), location, on='geolocation_zip_code_prefix')

df['order_delivered_customer_date'] = df['order_delivered_customer_date'].fillna('2016-10-11')
df['order_delivered_customer_date'] = df['order_delivered_customer_date'].fillna('2016-09-04')
df['order_purchase_timestamp'] = pd.to_datetime(df['order_purchase_timestamp']).dt.strftime('%Y')
df['order_delivered_customer_date'] = pd.to_datetime(df['order_delivered_customer_date']).dt.strftime('%Y')

df = df.drop_duplicates(subset=['order_id', 'product_category_name'])


In [13]:
df2 = pd.merge(orders, items, on='order_id')[['order_id', 'customer_id', 'product_id', 'order_status', 'order_purchase_timestamp', 'order_delivered_customer_date']].drop_duplicates()
df2 = pd.merge(df2, customers[["customer_id", 'customer_zip_code_prefix']], on='customer_id').drop_duplicates()
df2 = pd.merge(df2, products[["product_id","product_category_name"]], on='product_id').drop_duplicates()
df2 = pd.merge(df2.rename(columns={'customer_zip_code_prefix': 'geolocation_zip_code_prefix'}), location, on='geolocation_zip_code_prefix').drop_duplicates(subset=['product_category_name', 'geolocation_zip_code_prefix'])

df2['order_delivered_customer_date'] = df2['order_delivered_customer_date'].fillna('2016-10-11')
df2['order_delivered_customer_date'] = df2['order_delivered_customer_date'].fillna('2016-09-04')
df2['order_purchase_timestamp'] = pd.to_datetime(df2['order_purchase_timestamp']).dt.strftime('%Y')
df2['order_delivered_customer_date'] = pd.to_datetime(df2['order_delivered_customer_date']).dt.strftime('%Y')

df2 = df2.drop_duplicates(subset=['order_id', 'product_category_name'])


In [14]:
app = Dash(__name__)

colors = {
    'background': '#f0f7ff',
    'text': '#00336e'
}

fig_seller = px.scatter_mapbox(df, 
                        lat='geolocation_lat', 
                        lon="geolocation_lng", 
                        zoom=5, 
                        color='product_category_name',
                        mapbox_style="open-street-map",
                        text=df["geolocation_city"] + ', ' + df["geolocation_state"])

fig_seller.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)

fig_customer = px.scatter_mapbox(df2, 
                        lat='geolocation_lat', 
                        lon="geolocation_lng", 
                        zoom=5, 
                        color='product_category_name',
                        mapbox_style="open-street-map",
                        text=df2["geolocation_city"] + ', ' + df2["geolocation_state"])

fig_customer.update_layout(
    plot_bgcolor=colors['background'],
    paper_bgcolor=colors['background'],
    font_color=colors['text']
)

app.layout = html.Div([
    html.H1(children='Categories', style={'textAlign': 'center', 'color': '#8cc1ff'}),
    
    html.Div([
    html.H3(children='Pick a state', style={'textAlign': 'center', 'color': '#8cc1ff'}), 

    dcc.Dropdown(
        id='state-dropdown',
        options=[{'label': state, 'value': state} for state in df['geolocation_state'].unique()] + [{'label': 'Brazil', 'value': 'Brazil'}],
        value='Brazil'),
        
    html.H3(children='Pick date range', style={'textAlign': 'center', 'color': '#8cc1ff'}),

    dcc.DatePickerRange(
        id='date-slider',
        min_date_allowed='2016-01-01',
        max_date_allowed='2019-12-31',
        start_date='2016-01-01',
        end_date='2019-12-31')
    ], style={'width': '34%', 'display': 'inline-block', 'padding': '10px 5px'}),

    html.Div([
        html.H3(children='Pick statuses', style={'textAlign': 'center', 'color': '#8cc1ff'}),
        dcc.Checklist(
        id='status-checklist',
        options=[{'label': status, 'value': status} for status in df['order_status'].unique()],
        value=[df['order_status'].unique()[0]])
    ], 
        style={'width': '50%', 'display': 'inline-block',  'float': 'right', 'color': '#8cc1ff'}),

    html.Div([
        html.H2(children='Seller-categories', style={'textAlign': 'center', 'color': '#8cc1ff'}),
        dcc.Graph(
            id='seller-graph',
            figure=fig_seller),
        html.H2(children='Customer-categories', style={'textAlign': 'left', 'color': '#8cc1ff'}),
        dcc.Graph(
            id='customer-graph',
            figure=fig_customer)
    ], style={'display': 'inline-block', 'width': '99%'}),

])


@app.callback(
    Output('seller-graph', 'figure'),
    Output('customer-graph', 'figure'),
    Input('state-dropdown', 'value'),
    Input('status-checklist', 'value'),
    Input('date-slider', 'start_date'),
    Input('date-slider', 'end_date')
)
def update_graphs(state, statuses, start_date, end_date):
    if (state != 'Brazil'):
        dff = df[(df['geolocation_state'] == state) & (df['order_status'].isin(statuses))]
        dff2 = df2[(df2['geolocation_state'] == state) & (df2['order_status'].isin(statuses))]
    else:
        dff = df[(df['order_status'].isin(statuses))]
        dff2 = df2[(df2['order_status'].isin(statuses))]
        
    cust_filtered = dff[(dff['order_purchase_timestamp'] >= start_date) & (dff['order_delivered_customer_date'] <= end_date)]
    
    sales_fig = px.scatter_mapbox(cust_filtered, 
                        lat='geolocation_lat', 
                        lon="geolocation_lng", 
                        zoom=5, 
                        color='product_category_name',
                        mapbox_style="open-street-map",
                        text=cust_filtered["geolocation_city"] + ', ' + cust_filtered["geolocation_state"])

    
    cust_filtered = dff2[(dff2['order_purchase_timestamp'] >= start_date) & (dff2['order_delivered_customer_date'] <= end_date)]

    purchase_fig = px.scatter_mapbox(cust_filtered, 
                        lat='geolocation_lat', 
                        lon="geolocation_lng", 
                        zoom=5, 
                        color='product_category_name',
                        mapbox_style="open-street-map",
                        text=cust_filtered["geolocation_city"] + ', ' + cust_filtered["geolocation_state"])
    
    return sales_fig, purchase_fig


if __name__ == '__main__':
    app.run_server(debug=True) 

## Задание 5 (15 баллов)

Добавить карту, на котором можно будет посмотреть на количество продавцов или на количество покупателей (на него также должны работать фильтры по датам и по статусам, реализованные в прошлом занятии). Аггрегацию нужно делать по штатам. Чтобы вам помочь, вот snippet кода, который можно использовать для отображения:

In [15]:
import json
import pandas as pd
import plotly as plt
import plotly.express as px
from urllib.request import urlopen

# Brazil coordinates / shape
with urlopen(
    "https://raw.githubusercontent.com/codeforamerica/click_that_hood/master/public/data/brazil-states.geojson"
) as response:
    brazil = json.load(response)

# Since the database doesn't have an ID or feature using which values will be mapped between the coordinate/shape database and soybean database, we are adding an ID ourselves.
for feature in brazil["features"]:
    feature["id"] = feature["properties"]["sigla"]

# Здесь в качестве id, который будет отображаться, указано сокращение названия штата (как и в наших данных)

*Hint: обратите внимание, что покупатели и продавцы могут быть не во всех штатах, а эжто значит, что они могут не отображаться на карте. Эту ситуацию нужно обрабатывать и поправить*

## Задание 6 (15 баллов)

Сделайте карту кликабельной: по клику на штат должен показываться сам штат (и только он), все остальные графики обновляются по выбранному штату